<div style="border:1px solid black; padding:10px 10px;">
    <strong>How People Learn - Autumn 2019-2020</strong><br/>
    C. Hardebolle, R. Tormey - CC BY-NC-SA 4.0 Int.<br/><br/>
    <span style="text-decoration:underline;font-weight:bold;">How to use this notebook?</span>
    <ul style="margin:0;padding:0 0 0 20px;">
    <li>This notebook is made of text cells and code cells. The code cells have to be <strong>executed</strong> to see the result of the program. To execute a cell, simply select it and click on the "play" button (&#11208;) in the tool bar just above the notebook, or type <code>shift + enter</code>. It is important to execute the code cells in their order of appearance in the notebook.</li>
    <li>To improve readability, it can be useful to <strong>hide</strong> cells from the notebook (e.g. long code cells). To hide a cell, select it and click on the blue bar which appears on its left. To make the cell visible again, just click again on the blue bar, or on the three "dots" which represent the collapsed cell.</li></ul>
</div>

# Introduction to hypothesis testing

In this notebook we look at data on a type of flower called Iris and we analyze it using a programming language called Python.

## Learning goals

This notebook is designed for you to learn:
* How to distinguish between "population" datasets and "sample" datasets when dealing with experimental data
* How to compare a sample to a population using a statistical test called the "t-test" and interpret its results
* How to evaluate the magnitude of the difference between a sample and a population using a measure of the effect size called "Cohen's d" and interpret the results
* How to use Python scripts to make statistical analyses on a dataset

---

## Introduction

<div  style="width:300px;float:right;margin-left:15px;">
    <img src="figs/iris-picture.jpg" alt="iris virginica"/>

###### Iris virginica (Credit: Frank Mayfield CC BY-SA 2.0)

</div>

In 1935, an american botanist called Edgar Anderson worked on quantifying the morphologic variation of Iris flowers of three related species, Iris setosa, Iris virginica and Iris versicolor [[1]](#Bibliography). He realized a series of measures of the petal length, petal width, sepal length, sepal width and species.
Based on the combination of these four features, a British statistician and biologist named Ronald Fisher developed a model to distinguish the species from each other [[2]](#Bibliography).


### Question
A recent series of measurements has been carried out at the [Iris Garden of the Vullierens Castle](https://chateauvullierens.ch/en/) near Lausanne, on a sample of $n=50$ flowers of the Iris virginica species.  
**How similar (or different) is the Iris sample from the Vullierens Castle compared to the Iris virginica population documented by Edgar Anderson?**


###  Instructions  

**1. Read the notebook and execute the code cells**.   
To check your understanding, ask yourself the following questions:
* Can I explain how the concept of sample differs from the concept of population?
* What does a t-test tell me on my sample?
* What does Cohen's d tell me on my sample?

**2. Do the exercise** at the end of the notebook.  

&nbsp;

--- 

## Getting started

### Python tools for stats
Python comes with a number of libraries for processing data and computing statistics.
To use these tool you first have to load them using the `import` keyword.  
The role of the code cell just below is to load the tools that we use in the rest of the notebook. It is important to execute this cell *prior to executing any other cell in the notebook*.

In [ ]:
# plotting and display tools
%matplotlib inline
import matplotlib.pyplot as plt 
plt.style.use('seaborn-whitegrid') # global style for plotting

from IPython.display import display, set_matplotlib_formats
set_matplotlib_formats('svg') # vector format for graphs

# data computation tools
import numpy as np 
import pandas as pan
import math

# statistics tools
import scipy.stats as stats

### Data available on the Anderson dataset

Anderson has published summary statistics of his dataset.  
You have the mean petal length of the Iris virginica species: $\mu = 5.552$ cm.

In [ ]:
# Define mu as mean petal length of iris virginica species from Anderson
mu = 5.552

# Display mu
mu

### Data available on the Vullierens sample

You have the raw data collected on the petal length of the Vullierens sample, which is stored in the CSV file `iris-sample1-vullierens.csv` that you can see in the file explorer in the left pane.  
If you double click on the file it will open in a new tab and you can look at what is inside.

Now to analyze the data using Python you have to read the file:

In [ ]:
# Read the Vullierens sample data from the CSV file
sample_data = pan.read_csv('iris-sample1-vullierens.csv')

# Display the first few lines of the dataset
sample_data.head()

After reading the CSV file, its content is stored in the variable `sample_data`, which is a kind of table. Each line of the table is given an index number to identify it. We see above that, appart from the index, the table contains only one column, called `"petal_length"`, which contains all the measurements made on the Vullierens Irises. To get the list of all the values stored in that column, you can use the following syntax: `sample_data["petal_length"]`.

In [ ]:
# All values stored in the "petal_length" column of the "sample_data" table
sample_data["petal_length"]

&nbsp;

---

## First look at the data

### Descriptive statistics

Let's compute some simple descriptive statistics on this sample data. The `describe()` function gives us right away a number of useful descriptive stats:

In [ ]:
# Compute the descriptive stats
sample_stats = sample_data.describe()

# Display the result
sample_stats

You can access individual elements of the `sample_stats` table using the corresponding names for the line and column of the value.  
The following cell illustrates how to get the mean value of the petal length in the sample:

In [ ]:
# Extract the sample mean from the descriptive stats
sample_mean = sample_stats.loc["mean","petal_length"]

# Display the result
sample_mean

### Visualizations

Now let's make some simple visualisations of this data:

In [ ]:
# Create visualisation
fig = plt.figure(figsize=(16, 4))

# Plot the sample values
ax1 = plt.subplot(131)
ax1.set_xlabel('index of sample')
ax1.set_ylabel('petal length')
ax1.set_title("Samples")
ax1.plot(sample_data["petal_length"], 'go')
# Add the means
ax1.axhline(y=sample_mean, color='black', linestyle='-.', linewidth=1, label="sample mean $m$")
ax1.axhline(y=mu, color='black', linestyle=':', linewidth=1, label="$\mu$")
ax1.legend()

# Plot the distribution of the samples
ax2 = plt.subplot(132)
ax2.set_xlabel('petal length')
ax2.set_ylabel('number of samples')
ax2.set_title("Distribution")
ax2.hist(sample_data["petal_length"], color='green')
# Add the means
ax2.axvline(x=sample_mean, color='black', linestyle='-.', linewidth=1, label="sample mean $m$")
ax2.axvline(x=mu, color='black', linestyle=':', linewidth=1, label="$\mu$")
ax2.legend()

# Box plot with quartiles
ax3 = plt.subplot(133, sharey = ax1)
box = ax3.boxplot(sample_data["petal_length"], sym='k+', patch_artist=True)
ax3.set_ylabel('petal length')
ax3.set_title("Quartiles")
ax3.tick_params(axis='x', which='both', bottom=False, top=False, labelbottom=False)
plt.setp(box['medians'], color='black')
for patch in box['boxes']:
    patch.set(facecolor='green')
# Add the means
ax3.axhline(y=sample_mean, color='black', linestyle='-.', linewidth=1, label="sample mean $m$")
ax3.axhline(y=mu, color='black', linestyle=':', linewidth=1, label="$\mu$")
ax3.legend()

# Display the graph
plt.show()

As you can see, the Python code necessary to generate the graphs above is quite long. Hiding this particular code cell can improve the readability of the notebook. To hide it, select it and then click on the blue bar at its left. If you want to make the code visible again, simply click on the three "dots" or on the blue bar.


### Interpretation and hypothesis

The simple analyses we have made so far allow us to have a preliminary idea about how the Irises from Vullierens compare to those observed by Anderson. One feature to look at for the comparison is their respective mean petal length. We see above that the mean petal length $m$ of the Vullierens sample is quite close to the mean $\mu$ reported by Anderson.

Let's formulate this as an **hypothesis** which we state as: the sample mean $m$ is similar to the mean  of the reference population $\mu$, i.e. $m = \mu$. This hypothesis is noted $H_0$ and called the "null" hypothesis because it states that there is no difference between the sample and the population. 
The "alternate" hypothesis $H_a$ is that the sample mean is not similar to the mean of the reference population, $m \neq \mu$.

How can we test our hypothesis? In the following, we use a **statistical test** to answer this question.

&nbsp;

---

## Testing our hypothesis

In our hypothesis we compare the mean of one sample to a reference value. To test this hypothesis we can use a statistical test called a **one-sample t-test**.  

But what does it mean when we test the hypothesis that a sample mean is potentially equal to a given value?  

### Sample versus population

<div  style="width:500px;float:right;margin-left:15px;align:center;">
<img src="figs/diagram-samples.png" style="width:300px;margin-left:auto;margin-right:auto;display:block;"/>
<img src="figs/diagram-normalcurveAB.png" style="display:block;"/>
<img src="figs/diagram-normalcurveAlpha.png" style="display:block;"/>
</div>

To understand this, it is useful to start by thinking about a population, in this case our population of Irises which has a mean petal length of $\mu = 5.552$ cm.

Now imagine you take a sample of, say, 50 flowers from this population. The mean petal length of this sample is $m_1 = 6.234$ cm. You then take a second sample of 50, which ends up having a mean petal length of $m_2 = 5.874$ cm.  You then take a third sample of 50 which gives you a mean petal length of $m_3 = 5.349$ cm.

If you keep taking samples from this population, you will start to notice a pattern: while some of the samples will give a mean average length which is not at all close to the population mean, most of the mean petal lengths are reasonably close to the population mean of 5.552 cm. Furthermore, the mean average of the mean average of the samples will be the same as that of the population as a whole i.e. 5.552 cm.  

In fact, if we keep taking samples from this population, it turns out that the distribution of the average of these samples will take a very particular pattern that looks like a normal curve. In fact if you take bigger sample sizes (say 130 instead of 50) the distribution will get closer and closer to being a normal curve for which the mean average is equal to the mean average of the population. For these smaller samples, the distribution is called the **[Student's t-distribution](https://en.wikipedia.org/wiki/Student%27s_t-distribution)** (actually it is a family of distributions, which depend on the sample size).


This is useful because it allows us to rephrase our question as to how similar or different our sample from Vullierens Castle is to the population of Irises as described by Edgar Anderson. 
**What we have from the Vullierens Castle is a sample**. We want to know if it is a sample that might have come from a population like that described by Edgar Anderson. We now know the shape (more or less a normal distribution) and the mean (5.552 cm) of all of the samples that could be taken from the population described by Edgar Anderson. **So our question becomes "where does our sample fall on the distribution of all such sample means?"**.  
If our mean is in position A on the figure on the right, then it is plausible that our sample came from a population like that of Edgar Anderson.  If our mean is in position B, then it is less plausible to believe that our sample came from a population like Anderson’s.

### Cut-off point

You might be wondering, how far away is far enough away for us to think it is implausible that our sample comes from a population like Anderson’s. The answer is, it depends on how sure you want to be.  

One common answer to this question is to be 95% sure - meaning that a sample mean would need to be in the most extreme 5% of cases before we would think it is implausible that our sample comes from a population like Anderson’s ($\alpha=0.05$). These most extreme 5% cases are represented by the zones in light blue on the figure on the right. If the sample mean falls into these most extreme zones, we say that *the difference is "statistically significant"*.

A second, common answer is 99% sure meaning that a sample mean would need to be in the most extreme 1% of cases before we would think it is implausible that our sample comes from a population like Anderson’s ($\alpha=0.01$).   

In the following, **we will work on the basis of being 95% sure**. Let's define our $\alpha=0.05$:

In [ ]:
# Define alpha
alpha = 0.05

# Display alpha
alpha

If our distribution of sample means is a normal curve then we know that the most extreme 5% of sample means are found above or below ±1.96 standard deviations above and below the mean. In our case, because our sample size is less than 130 (it is 50), our distribution is close to normal but not quite normal. 
Still we can find out the relevant cut off point from looking it up in statistical tables: for a sample size of 50, the most extreme 5% of cases are found above or below 2.01 standard deviations from the mean. Let's define our cutoff point:

In [ ]:
# Define the cutoff point
cutoff = 2.01

# Display cutoff
cutoff

### Error in the distribution of means

So far we know a lot that will help us to test the hypothesis that our sample mean is similar to Anderson’s population mean. We know:
* Our sample mean $m$
* The population mean $\mu$
* The shape of the distribution of the mean of all samples that would come from this population (a normal curve, centred on the population mean)
* Our cut off point defined by $\alpha$ (the most extreme 5% of cases, above or below 2.01 standard deviations from the mean)

The last piece of information missing that would enable us to test this hypothesis is the size of the standard deviation of the distribution of sample means from Anderson’s population. 
It turns out that a good guess for the size of this standard deviation can be obtained from knowing the standard deviation of our sample.
If $s$ is the sample standard deviation of our sample and $n$ is the sample size, then the standard deviation of the distribution of sample means is:

$
\begin{align}
\sigma_{\overline{X}} = \frac{s}{\sqrt{n}}
\end{align}
$ 

This standard deviation of the distribution of sample means is called the "standard error of the mean" (also noted SEM).  
We can compute it by retrieving the sample size and standard deviation from the descriptive stats we have computed earlier:  

In [ ]:
# Extract the sample size from the descriptive stats generated earlier
sample_size = sample_stats.loc["count","petal_length"]

# Extract the sample standard deviation from the descriptive stats
sample_std = sample_stats.loc["std","petal_length"]

# Compute the estimation of the standard deviation of sample means from Anderson's population (standard error)
sem = sample_std / math.sqrt(sample_size)

# Display the standard error
sem

### Comparison

We can now restate our question in more precise terms: **"is our sample mean in the most extreme 5% of samples that would be drawn from a population with the same mean as Anderson’s population?"**.  
Or to be even more precise, **"is the gap between our sample mean and Anderson’s population mean greater than 2.01 times the standard error?"**. 

This would be equivalent to compare
$
\begin{align}
\frac{m - \mu}{\sigma_{\overline{X}}}
\end{align}
$
to our cutoff of 2.01. That is the definition of the **t** statistics: the value $t = $
$
\begin{align}
\frac{m - \mu}{\sigma_{\overline{X}}}
\end{align}
$ 
 has to be compared to the cutoff point we have chosen to determine if the sample mean falls into the most extreme zones and to be able to say whether the difference is statistically significant or not.
Let's compute $t$:

In [ ]:
# Compute the t statistics:
t = (sample_mean - mu) / sem

# Display t
print(t)

# Compare t with our cutoff point
if t > cutoff: 
    print("The difference is statistically significant.")
else: 
    print("The difference is not statistically significant.")

We see in the results above that for our Vullierens sample $t < 2.01$, therefore the difference between the two means is not greater than 2.01 times the standard error. In other words, our sample mean **is not in the most extremes 5%** of samples that would be drawn from a population with the same mean as Anderson's population.  

### Conclusion

What can we conclude from there? What the one sample t-test tells us is that we don't have evidence which would lead us to think that the sample doesn't come from an Anderson like population. Therefore we **cannot reject our hypothesis $H_0$**. However this is not the same to say that *it is* the same as the Anderson population. This is one of the limits of the t-test: like many other statistical tests, **it can be used only to reject an hypothesis**, not to confirm it.

&nbsp;

---

## Testing our hypothesis using a predefined Python function

So far we have made the computations by hand but Python comes with a number of libraries with interesting statistical tools. 
In particular, the `stats` library includes a function for doing a **one-sample t-test** as we have done above.  

### Computation of the test

Let's now use it and then look at what information it gives us.

In [ ]:
# Compute the t-test
t, p = stats.ttest_1samp(sample_data["petal_length"], mu)

# Display the result
print("t = {:.3f}".format(t))
print("p = {:.3f}".format(p))

The function returns two values `t` and `p` which say the same thing but in two different ways:
* `t` tells us where our sample mean falls on the distribution of all the possible sample means for the Anderson population ; `t` has to be compared to the `cutoff` value (2.01) to know if our sample mean is in the most extremes 5%.
* `p` (called the "p-value") is the probability to get a more extreme sample mean than the one we observe ; `p` has to be compared to `alpha` (0.05) to know if our sample mean is in the most extremes 5%.

### Interpretation of the results

We see above that `t < cutoff`, which means that the difference between the two means is smaller than 2.01 times the standard error and `p > alpha`, which means that the probability of getting more extreme sample mean than the one we observe is higher than 5% so it cannot be considered as one of the extreme possible values. Because they convey the same information, you can use either `t` or `p` to interpret the result of the t-test. In practice, most people use the p-value. 

As expected from the calculations we have made above, the test confirms that the difference between the mean petal length of the Vullierens sample and the mean petal length of Anderson's population is **not statistically significant**.

### Visualization

Using Python we can visualize what that means graphically by plotting the t-distribution of all the possible sample means that would be drawn from a population with the same mean as Anderson's population and showing where `t` is in the distribution compared to the zone defined by our $\alpha$ of 5%:

In [ ]:
# Create the t-test visualization
fig, ax = plt.subplots(figsize=(12, 4))
ax.set_title("Probability distribution of all possible sample means if $H_0$ is true")

# Let's plot the T distribution for this sample size
tdist = stats.t(df=sample_size, loc=0, scale=1)
x = np.linspace(tdist.ppf(0.0001), tdist.ppf(0.9999), 100)
y = tdist.pdf(x) 
ax.plot(x, y, color='blue', linewidth=1)

# Polish the look of the graph
ax.get_yaxis().set_visible(False) # hide the y axis
ax.set_ylim(bottom=0) 
ax.grid(False) # hide the grid 
ax.spines['top'].set_visible(False) # hide the frame except bottom line
ax.spines['right'].set_visible(False)
ax.spines['left'].set_visible(False)

# Plot the rejection zone two tailed
x_zone_1 = np.linspace(tdist.ppf(0.0001), tdist.ppf(alpha/2), 100)
x_zone_2 = np.linspace(tdist.ppf(1-alpha/2), tdist.ppf(0.9999), 100)
y_zone_1 = tdist.pdf(x_zone_1) 
y_zone_2 = tdist.pdf(x_zone_2) 
ax.fill_between(x_zone_1, y_zone_1, 0, alpha=0.3, color='blue', label = r'rejection of $H_0$ with $\alpha={}$'.format(alpha))
ax.fill_between(x_zone_2, y_zone_2, 0, alpha=0.3, color='blue')

# Plot the t-test stats
ax.axvline(x=t, color='green', linestyle='dashed', linewidth=1)
ax.annotate('t-test $t$={:.3f}'.format(t), xy=(t, 0), xytext=(-10, 130), textcoords='offset points', bbox=dict(boxstyle="round", facecolor = "white", edgecolor = "green", alpha = 0.8))

# Plot the p-value
if t >= 0: x_t = np.linspace(t, tdist.ppf(0.9999), 100)
else: x_t = np.linspace(tdist.ppf(0.0001), t, 100)
y_t = tdist.pdf(x_t) 
ax.fill_between(x_t, y_t, 0, facecolor="none", edgecolor="green", hatch="///", linewidth=0.0, label = r'p-value $p$={:.3f}'.format(p))

# Add a legend
ax.legend()

# Display the graph
plt.show()

&nbsp;

---

## Evaluating the magnitude of the difference between two means: effect size

So far we have tested our hypothesis regarding the similarity of means between our sample and the population and the results show us that there is probably no difference.
However whether this statistical test finds a difference depends on the sample size: with small samples it is harder to find a statistically significant difference.
We need therefore to **distinguish between a difference being statistically significant and a difference being large**.
The t-test is used to assess whether the difference is statistically significant. To assess whether the difference is large we use a measure called the effect size.

### Computation of the effect size

The effect size represents the size of the difference between the sample mean and the population mean taking into account the variation inside the sample (and inside the population, if known).  
Cohen's d is one of the existing measures of effect size. 
With $m$ and $s$ respectively the mean and standard deviation of the sample and $\mu$ the population mean, Cohen's d for one sample (when the standard deviation of the population $\sigma$ is not known) can be calculated as follows: 

$
\begin{align}
d = \frac{m - \mu}{s}
\end{align}
$

Let's compute the effect size of the difference between the Vullierens sample and Anderson's population:

In [ ]:
# Compute cohen's d
d = (sample_mean - mu)/sample_std

# Display the result
print("d = {:.3f}".format(d))

### Interpretation of the results

To interpret this result we have to **compare it to thresholds from the litterature**. Cohen suggested that $d=0.2$ was a small effect size, $0.5$ represents a medium effect size and $0.8$ represents a large effect size.
For our Vullierens sample the effect size is therefore small. In this case, the difference is also not statistically significant. However, with a larger sample size, it would be possible to have a statistically significant difference which nonetheless would be so small as to be trivial.


### Visualization

Let's visualize the result graphically (again, you can hide the lengthy code by clicking on the blue bar at its left).  
The graph below represents the theoretical distributions of the population in blue and of the sample in green. We see below that the two groups largely overlap, which is representative of the size of the difference being trivial.

In [ ]:
# Create the vizualisation for the effect size
fig, ax = plt.subplots(figsize=(8, 4))

# Plot the normal distribution
norm = stats.norm(loc=0, scale=1)
x = np.linspace(norm.ppf(0.0001), norm.ppf(0.9999), 100)
y = norm.pdf(x) 
ax.plot(x, y, color='blue', linewidth=1)
ax.axvline(x=0, color='blue', linestyle='dashed', linewidth=1)

# Plot the distribution of the sample
norm_d = stats.norm(loc=d, scale=1)
x_d = np.linspace(norm_d.ppf(0.0001), norm_d.ppf(0.9999), 100)
y_d = norm_d.pdf(x_d) 
ax.plot(x_d, y_d, color='green', linewidth=1)
ax.axvline(x=d, color='green', linestyle='dashed', linewidth=1)

# Display the value of Cohen's d
max_y = np.max(y)+.02
ax.plot([0,d], [max_y, max_y], color='red', linewidth=1, marker=".")
ax.annotate("effect size $d$={:.3f}".format(d), xy=(d, max_y), xytext=(15, -5), textcoords='offset points', bbox=dict(boxstyle="round", facecolor = "white", edgecolor = "red", alpha = 0.8))

# Display the graph
plt.show()

&nbsp;

---

## Summary

To summarize, to compare the mean of a sample to a reference value from a population, you have to proceed in four main steps:
1. formulate the hypothese you want to test: the null hypothesis $H_0: m = \mu$ and its alternate $H_a: m \neq \mu$ 
1. choose a cut-off point for being sure, usually $\alpha = .05$, $\alpha = .01$ or $\alpha = .001$ 
1. compute the result of the t-test and interpret the result - in particular if the p-value is *below* the significance level you have chosen, $p \lt \alpha$, then it means $H_0$ should probably be rejected
1. compute the effect size and interpret the result

&nbsp;

---

## Exercise

**A. Getting familiar with the code.**
1. In the code cells above, where is the t-test computed using the predefined Python function?
1. What are the two parameters that the t-test function takes as input?
1. If you wanted to change the population mean to a different value, like $\mu = 5.4$ cm for instance, in which cell would you change it?  
Then what would you need to do to update the result of the analysis in the notebook?
1. What is the result of the t-test if you compare the Vullierens sample to a population mean of $\mu = 5.4$ cm? And what is the effect size?

*Change the value of $\mu$ back to 5.552 before working on the following questions.*

**B. Analyzing another dataset.**

A researcher from Tokyo sends you the results of a series of measurements she has done on the Irises of the [Meiji Jingu Imperial Gardens](http://www.meijijingu.or.jp/english/nature/2.html). The dataset can be found in the `iris-sample2-meiji.csv` file.  
How similar (or different) is the Meiji sample compared to the Iris virginica population documented by Edgar Anderson?  
The following questions are designed to guide you in analyzing this new dataset using this notebook.

1. Which of the code cells above loads the data from the file containing the Vullierens dataset? Modify it to load the Meiji dataset.
1. Do you need to modify anything else in the code to analyze this new dataset?
1. What can you conclude about the Meiji sample from this analysis?

**C. Going a bit further in the interpretation of the t-test.**
1. In the code cells above, where is the cut-off point $\alpha$ defined? Change its value to 0.01 and re-execute the notebook. 
1. How does this affect the result of the t-test for the Meiji sample?

&nbsp;

*A solution of the exercise is available [in this file](solution/HPLstats_notebook-solution.ipynb).*

&nbsp;

---

<h2 id="Bibliography">Bibliography</h2>

[1] E. Anderson (1935). "The Irises of the Gaspe Peninsula." Bulletin of the American Iris Society 59: 2–5.

[2] R. A. Fisher (1936). "The use of multiple measurements in taxonomic problems". Annals of Eugenics. 7 (2): 179–188. doi:10.1111/j.1469-1809.1936.tb02137.x

More about the Iris Dataset on Wikipedia: https://en.wikipedia.org/wiki/Iris_flower_data_set

*Please note that the datasets used in this notebook have been generated using a random generator, they do not come from real measurement and cannot be used for any research purpose.*